In [6]:
from tqdm import tqdm
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from scipy.stats import norm, gamma
from scipy.stats._distn_infrastructure import rv_frozen
import matplotlib
from tqdm import tqdm
import mercury as mr
from IPython.display import HTML

np.seterr(divide='ignore', invalid='ignore')
matplotlib.rcParams["animation.embed_limit"] = 500

class Target:
    """
    π(x), the unnormalized target density (in this case Gamma dist).

    The true target is the posterior, but the normalizing constant cancels out anyways.
    """

    def __init__(self, v: float, alpha: float, beta: float, data: list):
        """
        Args:
            v (float): likelihood shape
            alpha (float): prior shape
            beta (float): prior rate
            data (list): likelihood data
        """
        self.v = v
        self.alpha = alpha
        self.beta = beta
        self.x = data
        self.n = len(data)

    def density(self, theta):
        """Unnormalized density of the Gamma distribution.

        Args:
            theta (np.ndarray): Values to evaluate the pdf at.

        Returns:
            np.ndarray: densities
        """
        return theta ** (self.v * self.n + self.alpha - 1) * np.exp(
            -theta * (self.beta + sum(self.x))
        )


class UpdateDist:
    """
    Used with matplotlib FuncAnimation function to create Metropolis visualization.

    This currently only does Metropolis random walk w/ N(0, proposal_variance).

    Modified from the Matplotlib docs at:
        https://matplotlib.org/stable/gallery/animation/bayes_update.html
    """

    def __init__(
        self,
        ax: matplotlib.axes.Axes,
        x_0: float,
        target: Target,
        true_posterior: rv_frozen,
        proposal_sigma: float,
        lower_bound: float,
        upper_bound: float,
        bins: int,
        seed: int,
    ):
        """

        Args:
            ax (matplotlib.axes.Axes)
            x_0 (float): initial value of the chain.
            target (Target): target density (need not be a true pdf)
            true_posterior (rv_frozen): true posterior, use scipy.stats dist
            proposal_sigma (float): Normal proposal std dev
            lower_bound (float): plot lower x limit
            upper_bound (float): plot upper x limit
            bins (int): histogram bins
            seed (int): random seed
        """
        assert lower_bound < upper_bound, "Lower bound must be less than upper bound."
        assert true_posterior.pdf(x_0) > 0.0, "Initial value density is 0."
        self.samples = []

        self.rng = np.random.default_rng(seed)
        self.init = x_0
        self.lower = lower_bound
        self.upper = upper_bound
        self.bins = bins
        self.parameter_values = np.linspace(lower_bound, upper_bound, 300)
        self.ax = ax
        self.proposal_sigma = proposal_sigma
        self.target = target
        self.true_posterior = true_posterior

        self.ax.set_xlim(lower_bound, upper_bound)
        self.ax.set_ylim(0, 1)

        self.ax.grid(True)
        (self.true_posterior_line,) = ax.plot(
            self.parameter_values,
            self.true_posterior.pdf(self.parameter_values),
            "r-",
            label="True Posterior",
        )
        self.ax.legend()

    def __call__(self, i):
        if i == 0:
            self.samples = []
            self.ax.clear()
            self.ax.grid(True)
            self.ax.set_xlim(self.lower, self.upper)
            self.ax.set_ylim(0, 1)
            (self.true_posterior_line,) = self.ax.plot(
                self.parameter_values,
                self.true_posterior.pdf(self.parameter_values),
                "r-",
                label="True Posterior",
            )
            return (self.true_posterior_line,)

        self.ax.clear()
        self.ax.grid(True)
        self.ax.set_xlim(self.lower, self.upper)
        self.ax.set_ylim(0, 1)

        proposal_mu = self.samples[-1] if self.samples else self.init
        proposed_value = norm.rvs(
            proposal_mu, self.proposal_sigma, random_state=self.rng
        )

        # plot
        proposal_density = norm.pdf(
            self.parameter_values, proposal_mu, self.proposal_sigma
        )
        (self.proposal_line,) = self.ax.plot(
            self.parameter_values, proposal_density, "g--", label="Proposal density"
        )

        # Metropolis acceptance criterion
        acceptance_ratio = self.target.density(proposed_value) / self.target.density(
            self.samples[-1] if self.samples else self.init,
        )

        (self.true_posterior_line,) = self.ax.plot(
            self.parameter_values,
            self.true_posterior.pdf(self.parameter_values),
            "r-",
            label="True Posterior",
        )

        self.ax.hist(
            self.samples,
            bins=self.bins,
            density=True,
            alpha=0.5,
            label="Sampled distribution",
        )

        if np.random.rand() >= acceptance_ratio:  # rejection
            self.ax.text(3.5, 0.5, "Rejection!", fontsize=12, color="red", ha="center")
            self.ax.scatter(
                [proposed_value],
                [0],
                c="r",
                s=50,
                label="Current proposal",
            )
        else:  # proposal accepted
            self.samples.append(proposed_value)
            self.ax.scatter(
                [proposed_value],
                [0],
                c="b",
                s=50,
                label="Current proposal",
            )

        self.ax.legend()
        return (self.true_posterior_line,)

app = mr.App(title="U5L6: Metropolis Gamma-Gamma Model",
        description="Random-walk Metropolis with a Gamma likelihood and Gamma prior.",
        show_code=False,
        show_prompt=False,
        continuous_update=False,
        static_notebook=False,
        show_sidebar=True,
        full_screen=True,
        allow_download=True)
_ = mr.Note(text="Gamma prior parameters")
alpha = mr.Numeric(value=1, min=0.1, max=10, label="α", step=0.1)
beta = mr.Numeric(value=1, min=0.1, max=10, label="β", step=0.1)
_ = mr.Note(text="Gamma likelihood shape")
v = mr.Numeric(value=1, min=0.1, max=10, label="v", step=0.1)
x = [1]
n = len(x)
_ = mr.Note(text="Algorithm options")
seed = mr.Numeric(value=1, min=0, max=2 ** 30, label="Random seed")
x_0 = mr.Numeric(value=1, min=0.1, max=5, label="x_0", step=0.1)
samples = mr.Slider(value=100, min=1, max=1000, label="samples", step=1)
proposal_sigma = mr.Numeric(
    value=0.4, min=0.1, max=2, label="Proposal standard deviation", step=0.1
)
_ = mr.Note(text="Plot options")
bins = mr.Slider(value=35, min=5, max=60, label="Histogram bins", step=1)

Gamma prior parameters

mercury.Numeric

mercury.Numeric

Gamma likelihood shape

mercury.Numeric

...

mercury.Numeric

mercury.Slider

mercury.Numeric

Plot options

mercury.Slider

In [7]:
mr.Markdown(
    text="""See [this page](https://areding.github.io/6420-pymc/unit5/Unit5-Metropolis.html) for the algorithm description.

Let our model be a Gamma-Gamma conjugate model, where:

$$
\\begin{align*}
X_i | \\beta &\\sim \\text{Ga}(v, \\theta) \\\\
\\theta &\\sim \\text{Ga}(\\alpha, \\beta)
\\end{align*}
$$

We'll just have a single datapoint, $x=1$, for simplicity.

For our target $\\pi(x)$, we have:

$$\pi(\\theta|x) \\propto \\theta^{vn + \\alpha - 1} e^{-\\theta(\\beta + \\sum_{i=1}^{n}X_i)}$$

Our true posterior by conjugacy is:

$$Ga(\\alpha + nv, \\beta + \\sum_{i=1}^{n}X_i)$$

We'll use a $N(0, \\sigma^2)$ proposal.
"""
)

See [this page](https://areding.github.io/6420-pymc/unit5/Unit5-Metropolis.html) for the algorithm description.

Let our model be a Gamma-Gamma conjugate model, where:

$$
\begin{align*}
X_i | \beta &\sim \text{Ga}(v, \theta) \\
\theta &\sim \text{Ga}(\alpha, \beta)
\end{align*}
$$

We'll just have a single datapoint, $x=1$, for simplicity.

For our target $\pi(x)$, we have:

$$\pi(\theta|x) \propto \theta^{vn + \alpha - 1} e^{-\theta(\beta + \sum_{i=1}^{n}X_i)}$$

Our true posterior by conjugacy is:

$$Ga(\alpha + nv, \beta + \sum_{i=1}^{n}X_i)$$

We'll use a $N(0, \sigma^2)$ proposal.


In [10]:
true_posterior = gamma(a=alpha.value + n * v.value, scale=1.0 / (beta.value + sum(x)))
target = Target(v.value, alpha.value, beta.value, data=x)

threshold = 0.999
upper_bound = round(true_posterior.ppf(threshold))

fig, ax = plt.subplots()

ud = UpdateDist(
    ax,
    x_0.value,
    target,
    true_posterior,
    proposal_sigma=.4,
    lower_bound=0.0,
    upper_bound=5.0,
    bins=bins.value,
    seed=int(seed.value),
)


plt.close()

In [11]:
anim = FuncAnimation(fig, ud, frames=samples.value, interval=100, blit=True)
HTML(anim.to_jshtml())